pip install plotly-express - to musiałam zainstalować w cmd

### Importy:

In [1]:
import pandas as pd
import plotly.express as px
import pandas as pd
import matplotlib.pyplot as plt
import geopandas as gpd
import numpy as np
import folium
from folium.features import GeoJsonTooltip

In [2]:
tmp_df = pd.read_csv('akutalne_dane_wojewodztwa.csv')

In [3]:
woj = tmp_df['wojewodztwo'].values.tolist()
del woj[0]

In [4]:
zgony = [7561, 7343, 7918, 3212, 8214, 9559, 14802, 3422, 7225, 3717, 6702, 14225, 4203, 4660, 10680, 4736]
kod_iso = ['PL-02', 'PL-04', 'PL-06', 'PL-08', 'PL-10', 'PL-12', 'PL-14', 'PL-16', 'PL-18', 'PL-20', 'PL-22', 
          'PL-24', 'PL-26', 'PL-28', 'PL-30', 'PL-32']

In [5]:
df = pd.DataFrame(list(zip(woj, zgony, kod_iso)),
               columns =['wojewodztwo', 'zgony', 'ISO'])

In [6]:
geojson = gpd.read_file(r'wojewodztwa-max.geojson')

In [7]:
geodf = geojson.drop(['id'], axis = 1)
kody_geo = ['PL-24', 'PL-16', 'PL-30', 'PL-32', 'PL-26', 'PL-04', 'PL-20', 'PL-02', 'PL-18', 
           'PL-12', 'PL-22', 'PL-28', 'PL-10', 'PL-14', 'PL-06', 'PL-08']

geodf['Kod'] = kody_geo

In [8]:
df_final = geodf.merge(df, left_on="nazwa", right_on="wojewodztwo", how="outer") 

In [9]:
pl_map = folium.Map(location=[52.1667, 19.3667], zoom_start=4,tiles='openstreetmap')

In [10]:
#Create the choropleth map add it to the base map
covid = df_final['zgony'].values.tolist()
covid_max = max(covid)

custom_scale1 = [0,4000,7000,10000,covid_max],

folium.Choropleth(
            geo_data= geodf,
            data= df_final,
            columns=['ISO', 'zgony'],  
            key_on='feature.properties.Kod', #Here we grab the geometries/county boundaries from the geojson file using the key 'coty_code' which is the same as county fips
            threshold_scale=custom_scale1[0], #use the custom scale we created for legend
            fill_color='PuRd',
            nan_fill_color="Black", #Use white color if there is no data available for the county
            fill_opacity=0.7,
            line_opacity=0.2,
            legend_name='Liczba zgonów w danym województwie', #title of the legend
            highlight=True,
            line_color='black').add_to(pl_map) 

pl_map.save(outfile= "polska_smierci.html")
pl_map

### Źródła: 
- https://koronawirusunas.pl/
- https://github.com/ppatrzyk/polska-geojson
